In [1]:
import dataset
import importlib
import json
import numpy as np
import os
import reasoning
import torch
import qa
import time

from dataset.bgquiz import BGQuiz
from datetime import datetime
from elasticsearch import Elasticsearch
from elasticsearch import helpers
from pytorch_pretrained_bert import BertTokenizer, BertModel, BertForQuestionAnswering, BertForMultipleChoice
from reasoning.multichoice import *
from tqdm import tqdm
from qa.utils import query_es
from qa.wiki_abstracts import get_wiki_abstracts


# Reload the cached modules
_ = importlib.reload(dataset.bgquiz)
_ = importlib.reload(qa.utils)
_ = importlib.reload(reasoning.multichoice)

In [2]:
model_dir = "models/RACE_BERT"

# Example for a Bert model
model = BertForMultipleChoice.from_pretrained(model_dir, num_choices=4)
model.to('cuda')

BertForMultipleChoice(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(119547, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): FusedLayerNorm(torch.Size([768]), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): FusedLayerNorm(torch.Size([768]), eps=1e-12, elementwise_

In [3]:
tokenizer = BertTokenizer.from_pretrained(model_dir, do_lower_case=False)  # Add specific options if needed

In [4]:
wiki_control = \
'''
Обсадата на Одрин приключва с превземането на турската крепост от Втора българска армия под общото командване на ген. Никола Иванов. Решителният пробив на източния сектор на крепостта е извършен под командването на ген. Георги Вазов. Ръководещият защитата на Одрин – Шукри паша, предава сабята си на ген. Иванов с думите: „Храбростта на българската армия е безподобна. На такава храброст никоя крепост не може да устои“. Победата фактически решава изхода на Балканската война.
'''

question_control = "Кои военачалници ръководят защитата и превземането на Одринската крепост през месец март 1913 г.?"
options_control = [
         "Абдулах паша – ген. Радко Димитриев",
         "Явер паша – ген. Васил Кутинчев",
         "Назим паша – ген. Данаил Николаев",
         "Шукри паша – ген. Никола Иванов"
      ]

question_control = \
'''
Името на коя международна организация е пропуснато в текста от нейния Устав, 
подписан през 1945 г. в Сан Франциско?    
„1. _____________________________ е основана върху принципа на пълното равенство на  своите членове. 
3. Те се задължават да уреждат международните си спорове с мирни  средства. 
4. Членовете се въздържат в отношенията си от заплаха или от употреба на  сила. 
7. Организацията не се намесва във вътрешните работи на държавите. 
Това обаче не  засяга прилагането на принудителни мерки в случай на заплаха срещу мира, 
на нарушение на  мира и на актове на агресия.”'''
wiki_control = '''
Никола Иванов (генерал)\n\nНикола Иванов Иванов е български офицер (генерал от пехотата), началник на Щаба на войската през 1894–1896 година и министър на войната (1896–1899). Командир на Втора българска армия през Балканските войни от 1912–1913 година. Ръководи обсадата и превземането на Одринската крепост (март 1913).\n\nНикола Иванов е роден на 2 март 1861 г. в Калофер. Учи в Априловската гимназия '''
options_control = [
         "Лигата на нациите",
         "Организацията на обединените нации",
         "Международната агенция за атомна енергия",
         "Международната организация на труда"
      ]


        
predict(model, tokenizer, wiki_control, question_control, options_control, use_gpu=True)

array([[-0.09922   , -0.23784254, -0.12615059,  0.05656043]])

In [5]:
es = Elasticsearch()
name = "bgwiki_paragraph"

In [6]:
quiz = BGQuiz("data/bg_rc-v1.0.json")

In [7]:
!polyglot download embeddings2.bg
!polyglot download embeddings2.sr
!polyglot download embeddings2.ru

!polyglot download ner2.bg
!polyglot download ner2.sr
!polyglot download ner2.ru

!polyglot download pos2.bg


[polyglot_data] Downloading package embeddings2.bg to
[polyglot_data]     /home/desi/polyglot_data...
[polyglot_data]   Package embeddings2.bg is already up-to-date!
[polyglot_data] Downloading package embeddings2.sr to
[polyglot_data]     /home/desi/polyglot_data...
[polyglot_data]   Package embeddings2.sr is already up-to-date!
[polyglot_data] Downloading package embeddings2.ru to
[polyglot_data]     /home/desi/polyglot_data...
[polyglot_data]   Package embeddings2.ru is already up-to-date!
[polyglot_data] Downloading package ner2.bg to
[polyglot_data]     /home/desi/polyglot_data...
[polyglot_data]   Package ner2.bg is already up-to-date!
[polyglot_data] Downloading package ner2.sr to
[polyglot_data]     /home/desi/polyglot_data...
[polyglot_data]   Package ner2.sr is already up-to-date!
[polyglot_data] Downloading package ner2.ru to
[polyglot_data]     /home/desi/polyglot_data...
[polyglot_data]   Package ner2.ru is already up-to-date!
[polyglot_data] Downloading package pos2.bg to

In [8]:
from qa.wiki_abstracts import get_wiki_abstracts


query_fields = [
#     ['title.bulgarian', 'passage.bulgarian'],
#     ['title.bulgarian', 'passage.ngram'],
#     ['title.bulgarian', 'passage.ngram', 'passage', 'passage.bulgarian'],
#     ['passage.ngram', 'passage', 'passage.bulgarian^2'],
    ['title.bulgarian^2', 'passage.ngram', 'passage', 'passage.bulgarian^2'],
]

for query_field in query_fields:
    #, 'bgwiki_window'
    for name in ['bgwiki_paragraph']:
        for cr in [2]:
            start = time.time()
            
            setup = dict()
            setup['results_count'] = cr
            setup['query_field'] = query_field.copy()
            setup['index'] = name
            setup['model'] = model_dir

            print(json.dumps(setup, indent=2))
            print()

            preds = {}

            for i, q in enumerate(quiz.iterator()):
                question = q.question
                answers = q.answers

                try:
                    passages = set()
                    for a in answers:
                        passages.update([
                            x['source']['passage'] for x in query_es(
                                es, question + ' ' + a, setup['index'],
                                setup['results_count'], setup['query_field'])
                        ])
                    
                    # Adding wikipedia passages
                    
                    print('QUESTION IS')
                    print(question)
                    
                    question_abstracts = get_wiki_abstracts([question])
                    question_abstracts = question_abstracts[0] if len(question_abstracts) > 0 else ''
                    answers_abstracts = get_wiki_abstracts(answers)

                    passages = list(map(lambda x: x[0] + ' ' + x[1],
                                        zip(passages, [question_abstracts + ' ' + a for a in answers_abstracts])))

                    ans_cnt = len(answers)
                    if ans_cnt < 4:
                        answers.append(' ')

                    votes = np.zeros(4, dtype=np.int32)
                    sc = np.ones((1, 4), dtype=np.float32)
                    for p in passages:
                        scores = predict(
                            model, tokenizer, p, question, answers, use_gpu=True)
                        if ans_cnt < 4:
                            scores[0, 3] = -np.inf
                        sc += softmax(scores)

                        votes[scores.argmax()] += 1

    #                 print(str(i + 1) + './' + str(len(quiz.data_gen)), question)
    #                 print(answers, q['correct'])
    #                 print(answers[sc.argmax()], votes)

                    preds[q.id] = answers[sc.argmax()]

                    #                 print()

                    print(str(i + 1) + './' + str(quiz.size()), end='...')
                except KeyboardInterrupt:
                    raise

            print()
            dirname = str(int(datetime.now().timestamp()))
            path = 'experiments/{}'.format(dirname)
           
            try:
                if not os.path.exists(path):
                    os.makedirs(path)
            except OSError:
                print("Creation of the directory %s failed" % path)
            else:
                print("Successfully created the directory %s " % path)

            with open(path + '/preds.json', 'w') as o:
                json.dump(preds, o, ensure_ascii=False)

            with open(path + '/setup.json', 'w') as o:
                json.dump(setup, o, ensure_ascii=False, indent=2)
                
            

            print(path)
            !python evaluation/evaluate.py data/bg_rc-v1.0.json $path/preds.json  --out-file $path/eval.json
            
            end = time.time()
            print("Done in {} seconds", int(end - start))

{
  "results_count": 2,
  "query_field": [
    "title.bulgarian^2",
    "passage.ngram",
    "passage",
    "passage.bulgarian^2"
  ],
  "index": "bgwiki_paragraph",
  "model": "models/RACE_BERT"
}

QUESTION IS
Самостоятелно съществуващи живи системи са:
Entity found системи


Detector is not able to detect the language reliably.


abstract's length is 203 
Система се нарича множество от обекти и връзки между тях, които се разглеждат като едно цяло. Една връзка може да свързва два или повече обекта. Тя може да бъде информационна, материална или енергийна...
Entity found вирусите


Detector is not able to detect the language reliably.


abstract's length is 206 
Вирусът (на латински: virus – „отрова“) е микроскопичен патоген, който инфектира клетки в живи организми. Вирусите могат да се възпроизвеждат единствено като подчиняват и контролират други клетки, понеже...
Entity found тъканите


...

Entity found стена
abstract's length is 208 

Стената е плътна, най-често вертикална, конструкция, която отделя или защитава дадено пространство. Най-често стените разделят пространството в сградите на стаи или разграничават пространството на открито...
Entity found ['Нагасаки']
Entity found бомбардировка
abstract's length is 423 
Нагасаки или Нагазаки ( произношение, по английската Система на Хепбърн Nagasaki-shi, Нагасаки-ши) е столицата и най-големият град в префектура Нагасаки в Япония. Населението му е 416 419 жители (по приблизителна...
Бомбардировка (на френски: bombardement) (бомбено нападение, бомбен рейд) е обстрелване с артилерия хвърляне бомби от самолет или организирано масово нападение на бомбардировачи над противникова територия...
1961./2633...QUESTION IS
Заедно с коя друга държава България е приета в Европейския съюз?
Entity found ['България', 'Европейския']
Entity found държава
Entity found съюз


Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.
Detector is not able to detect the language reliably.


abstract's length is 437 
Европейският съюз (съкратено ЕС, Евросъюз) е международна организация, политически и икономически съюз между 28 европейски държави. Той е самостоятелно юридическо лице, притежаващо правомощия да действа...
Държава (или разговорно, но ограничено по обхват, страна) е политически организирана общност, заемаща дадена територия, имаща правителство (система за управление) и притежаваща вътрешен и външен суверенитет...
Съюз
Съюз
Союз
Союз-У
Entity found ['Румъния']
abstract's length is 206 
Румъ̀ния (на румънски: România) е държава в Югоизточна Европа. Тя граничи на североизток с Молдова и Украйна, на запад – с Унгария и Сърбия, а на юг – с България. На изток има излаз на Черно море. Площта...
Entity found ['Гърция']
abstract's length is 204 
Гъ̀рция, официално Република Гърция  (на гръцки: Ελλάδα, Елада или катаревуса: Ελλάς, Елас, пълно име: Ελληνική Δημοκρατία, Елиники Димократия, Гръцка република), е държава в Югоизточна Европа, заемаща...
Entity found ['Чехия']


Entity found разрешение
Entity found папата
Entity found църква
abstract's length is 630 
Папа Римски (на латински: papa, и на гръцки: πάππας – в пр. отец, баща) е глава и върховен суверенен йерарх (понтифекс, понтифик) (на латински: Pontifex Romanus – римски понтифекс, или на латински: Pontifex...

Папа Римски (на латински: papa, и на гръцки: πάππας – в пр. отец, баща) е глава и върховен суверенен йерарх (понтифекс, понтифик) (на латински: Pontifex Romanus – римски понтифекс, или на латински: Pontifex...
Църква или черква е храм, в който се отслужват християнски богослужения.


== Етимология ==
Българската дума църква произхожда от старобългарската дума црькы, произлязла от праславянската *сьrky. Тя от своя...
Entity found въпроса
Entity found покръстването
Entity found българите
abstract's length is 423 

Християнизацията е широкообхватен обществен феномен в световната история. Изразява се в подмяната на традиционните религии на определени общества или народи от различни форми на хри

KeyboardInterrupt: 

In [9]:
dirname = str(int(datetime.now().timestamp()))
path = 'experiments/{}'.format(dirname)

try:
    if not os.path.exists(path):
        os.makedirs(path)
except OSError:
    print("Creation of the directory %s failed" % path)
else:
    print("Successfully created the directory %s " % path)

with open(path + '/preds.json', 'w') as o:
    json.dump(preds, o, ensure_ascii=False)

with open(path + '/setup.json', 'w') as o:
    json.dump(setup, o, ensure_ascii=False, indent=2)



print(path)
!python evaluation/evaluate.py data/bg_rc-v1.0.json $path/preds.json  --out-file $path/eval.json

end = time.time()
print("Done in {} seconds", int(end - start))

Successfully created the directory experiments/1560647798 
experiments/1560647798
Done in {} seconds 13753


In [ ]:
from polyglot.text import Text


t = Text("Редуцентите са организми, които се хранят:", hint_language_code='bg')

In [ ]:
t.pos_tags

In [ ]:
list(filter(lambda x: x[1] == 'NOUN', t.pos_tags))